## Introduction

This notebook illustrates how to use DeepFrag as an API. For command-line use, see the examples in `./tests/run_tests.sh`.

The notebook doesn't describe how to train a new Deefrag model from scratch. Instead, it descsribes how to use an already trained checkpoint for inference, and how to finetune that checkpoint.

The `./tests/run_tests.sh` script generates sample checkpoint files. Note that these checkpoints are not well trained and should not be used in production. The checkpoint files are not included in the git repo, but this notebook assumes they exist. Be sure to run `./tests/run_tests.sh` before using this notebook, or change the checkpoint paths to your own files.


In [1]:
# Start by importing the needed libraries

import torch
import pytorch_lightning as pl
import os
from apps.deepfrag.run import DeepFrag
from argparse import Namespace

# Confirm the torch and lightning versions
print(torch.__version__)
print(pl.__version__)

INFO: Note: NumExpr detected 36 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.


collagen.GraphMol requires torch_geometric!
1.11.0
1.5.10


In [2]:
# Make a working directory if needed

os.system("mkdir -p tmp_working_dir")

0

In [3]:
# Create the deepfrag model

model = DeepFrag()

INFO: ProDy is configured: verbosity='none'


## Inference on a single protein/ligand complex

In [4]:
# Define the deepfrag parameters. These are the same parameters available through the commandline.

from collagen.args_defaults import add_missing_args_to_namespace

def get_args_for_inference_example(ckpt):
    args = Namespace(
        mode="inference",
        receptor="./tests/data_for_inference/5VUP_prot_955.pdb",
        branch_atm_loc_xyz="12.413000, 3.755000, 59.021999",
        ligand="./tests/data_for_inference/5VUP_lig_955.sdf",
        load_checkpoint=ckpt,
        default_root_dir="./tmp_working_dir/",
        rotations=2,
        inference_label_sets="./tests/data_for_inference/label_set.smi",
        num_inference_predictions=10,
        fragment_representation="rdk10",

        # Boilerplate
        log_every_n_steps=25,
        num_dataloader_workers=32,
        gpus=1,
        verbose=True,
    #     aggregation_rotations="mean"
    )
    args = add_missing_args_to_namespace(args)
    
    # Setup the fingerprint scheme. This makes some updates to the args depending on whether you're using
    # rdk10 or molbert fingerprints.
    model.setup_fingerprint_scheme(args)
    
    return args
args = get_args_for_inference_example("./tests/1.train_on_moad.output/last.ckpt")

In [5]:
# Load the checkpoint

ckpt = model.load_checkpoint(args, validate_args=False)

Restoring from checkpoint: ./tests/1.train_on_moad.output/last.ckpt


### Using the `run_inference()` helper function

In [6]:
# Deepfrag includes a helper function that runs inference, calculates the
# average output vector over multiple rotations, and selects the top-K most
# similar fragments.

# Third argument is save_results_to_disk. If False, returns results instead of
# saving to disk.

result = model.run_inference(args, ckpt, False)

Using the operator mean to aggregate the inferences.


DEBUG: 7165 atoms and 1 coordinate set(s) were parsed in 0.07s.
INFO: Created a temporary directory at /tmp/tmpu8d3s6wn
INFO: Writing /tmp/tmpu8d3s6wn/_remote_module_non_sriptable.py


Using checkpoint ./tests/1.train_on_moad.output/last.ckpt

Loading model from checkpoint ./tests/1.train_on_moad.output/last.ckpt

    Rotation #1
    Rotation #2


/gpfs/workspace/users/durraj/deepfrag2/collagen/core/molecules/mol.py:443: UserWarning: Internal rdmol has no conformers
  warnings.warn("Internal rdmol has no conformers")


Label set size: 556


Most Similar Matches:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
# The most similar fragments from your label set

result["most_similar"]

[['*CC', 0.6476905941963196],
 ['*CCN', 0.6222891211509705],
 ['*C(C)N', 0.5784493684768677],
 ['*CC#C', 0.547858476638794],
 ['*CCC', 0.5347429513931274],
 ['*CCCN', 0.5337764620780945],
 ['*CC=C', 0.5302090644836426],
 ['*C(C)C', 0.5226818323135376],
 ['*CCO', 0.5145487785339355],
 ['*C(C)O', 0.5029493570327759]]

In [8]:
# The Deepfrag output fingerprints, per rotation

print("First-rotation fingerprint:", result["fps"]["per_rot"][0])
print("")
print("Total fingerprints:", len(result["fps"]))

First-rotation fingerprint: tensor([[6.4081e-04, 6.9047e-05, 7.3328e-04,  ..., 2.1784e-05, 7.6565e-05,
         8.1814e-01]], grad_fn=<SigmoidBackward0>)

Total fingerprints: 2


In [9]:
# The average fingerprint over all rotations

print("Average fingerprint:", result["fps"]["avg"])

Average fingerprint: tensor([[8.3699e-04, 9.8438e-05, 9.7834e-04,  ..., 3.2347e-05, 1.1116e-04,
         8.1603e-01]], grad_fn=<MeanBackward1>)


### Without the `run_inference()` helper function

In [10]:
# You don't have to use the helper function if you'd
# like more customized use. Here is an example.

# First, load the receptor and ligand

import prody
from rdkit import Chem
from collagen.core.molecules.mol import Mol
from io import StringIO
import numpy as np

# Load the receptor
with open(args.receptor, "r") as f:
    m = prody.parsePDBStream(StringIO(f.read()), model=1)
prody_mol = m.select("all")
recep = Mol.from_prody(prody_mol)

# Load the ligand
suppl = Chem.SDMolSupplier(str(args.ligand))
rdmol = [x for x in suppl if x is not None][0]
lig = Mol.from_rdkit(rdmol, strict=False)

# Calculate the center of the receptor. 
center = np.array([float(v.strip()) for v in args.branch_atm_loc_xyz.split(",")])

DEBUG: 7165 atoms and 1 coordinate set(s) were parsed in 0.07s.


In [11]:
# Voxelize the receptor and ligand

from collagen.util import rand_rot

# Get a random rotation
rot = rand_rot()

# Get the parameters to use when voxelizing the protein and ligand.
voxel_params = model.init_voxel_params(args)

# Voxelize the receptor
recep_vox = recep.voxelize(
    voxel_params, cpu=True, center=center, rot=rot
)

# Voxelize the ligand
lig_vox = lig.voxelize(voxel_params, cpu=True, center=center, rot=rot)

# Stack the receptor and ligand tensors
num_features = recep_vox.shape[1] + lig_vox.shape[1]
dimen1 = lig_vox.shape[2]
dimen2 = lig_vox.shape[3]
dimen3 = lig_vox.shape[4]
vox = torch.cat([recep_vox[0], lig_vox[0]]).reshape(
    [1, num_features, dimen1, dimen2, dimen3]
)

In [12]:
# Initialize the model

# Set the device (e.g., cuda)
device = model.init_device(args)

model_initialized = model.init_model(args, ckpt)

model_initialized.eval()


Loading model from checkpoint ./tests/1.train_on_moad.output/last.ckpt



DeepFragModel(
  (encoder): Sequential(
    (0): BatchNorm3d(10, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (1): Conv3d(10, 64, kernel_size=(3, 3, 3), stride=(1, 1, 1))
    (2): ReLU()
    (3): Conv3d(64, 64, kernel_size=(3, 3, 3), stride=(1, 1, 1))
    (4): ReLU()
    (5): Conv3d(64, 64, kernel_size=(3, 3, 3), stride=(1, 1, 1))
    (6): ReLU()
    (7): MaxPool3d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
    (8): BatchNorm3d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (9): Conv3d(64, 64, kernel_size=(3, 3, 3), stride=(1, 1, 1))
    (10): ReLU()
    (11): Conv3d(64, 64, kernel_size=(3, 3, 3), stride=(1, 1, 1))
    (12): ReLU()
    (13): Conv3d(64, 64, kernel_size=(3, 3, 3), stride=(1, 1, 1))
    (14): ReLU()
    (15): Aggregate3x3Patches(output_size=(1, 1, 1))
    (16): Flatten(start_dim=1, end_dim=-1)
    (17): Dropout(p=0.5, inplace=False)
    (18): Linear(in_features=64, out_features=512, bias=True)
    (19):

In [13]:
# Predict the appropriate fingerprint given these voxel inputs.

fp = model_initialized.forward(vox)
fp

tensor([[2.8038e-04, 2.6546e-05, 4.1705e-04,  ..., 7.4562e-06, 2.6024e-05,
         8.3876e-01]], grad_fn=<SigmoidBackward0>)

In [14]:
# To find the closest fragments to the output fingerprint, we must
# prepare our inference label set. There's a helper function for that:

(
    label_set_fingerprints,
    label_set_entry_infos,
) = model.create_inference_label_set(
    args,
    device,
    [l.strip() for l in args.inference_label_sets.split(",")],
)

Label set size: 556


In [15]:
# Now use another helper function to find the most similar matches.

from collagen.metrics.metrics import most_similar_matches

most_similar = most_similar_matches(
    fp,
    label_set_fingerprints,
    label_set_entry_infos,
    args.num_inference_predictions,  # self.NUM_MOST_SIMILAR_PER_ENTRY,
)

most_similar

Most Similar Matches:   0%|          | 0/1 [00:00<?, ?it/s]

[[['*CC', 0.6511650085449219],
  ['*CCN', 0.6218820214271545],
  ['*C(C)N', 0.5774090886116028],
  ['*CC#C', 0.5500320196151733],
  ['*CC=C', 0.532761812210083],
  ['*CCC', 0.5288671255111694],
  ['*CCCN', 0.5265183448791504],
  ['*C(C)C', 0.5204364657402039],
  ['*CCO', 0.5094911456108093],
  ['*C(=C)C', 0.49325859546661377]]]

## Finetuning

When you train a Deepfrag model from scratch (using the CLI), it produces not only a `ckpt` file, but also a `pt` file. The `pt` file is useful for finetuning a Deepfrag model.

Note that finetuning is also called "warm starting."

In [16]:
# We must define new arguments for this new task.

os.system("mkdir -p ./tmp_working_dir/finetuned/")
    
args = Namespace(
    mode="warm_starting",
    model_for_warm_starting="./tests/1.train_on_moad.output/model_mean_mean_train.pt",    
    default_root_dir="./tmp_working_dir/finetuned/",
    max_epochs=5,
    fragment_representation="rdk10",
    butina_cluster_cutoff=0.4,

    # Directory contains protein/ligands named like 1XDN_prot_123.pdb, 1XDN_lig_123.sdf
    data_dir="./tests/data_to_finetune/",
    
    # In this case, let's have no validation set.
    fraction_val=0.0,
    
    # Boilerplate
    log_every_n_steps=25,
    num_dataloader_workers=32,
    cache_pdbs_to_disk=True,
    gpus=1,
)

# The fp_size parameter depends on which fragment_representation you use. You can set it
# explicitly, or use a helper function to pick the appropriate one.

from collagen.model_parents.moad_voxel.moad_voxel import MoadVoxelModelParent
MoadVoxelModelParent.setup_fingerprint_scheme(args)
print(args.fp_size)

args = add_missing_args_to_namespace(args)


2048


In [17]:
model.run_warm_starting(args)

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs


Building training/validation/test sets based on Butina clustering
Training dataset size: 674
Validation dataset size: 0
Test dataset size: 482
Building/updating dataset


Runtime filters: 100%|█████████████████████| 674/674 [00:00<00:00, 66415.15it/s]


Number of fragments in the TRAIN set: 1749
Number of batches for the training data: 110


/home/durraj/miniconda3/envs/deepfrag/lib/python3.8/site-packages/pytorch_lightning/trainer/configuration_validator.py:122: UserWarning: You defined a `validation_step` but have no `val_dataloader`. Skipping val loop.
  rank_zero_warn("You defined a `validation_step` but have no `val_dataloader`. Skipping val loop.")
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Set SLURM handle signals.

  | Name                   | Type       | Params
------------------------------------------------------
0 | encoder                | Sequential | 604 K 
1 | deepfrag_after_encoder | Sequential | 1.1 M 
------------------------------------------------------
1.7 M     Trainable params
0         Non-trainable params
1.7 M     Total params
6.619     Total estimated model params size (MB)


...

INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 27248 bytes
INFO: dealloc: cuMemFree_v2 27264 bytes
INFO: dealloc: cuMemFree_v2 27264 bytes
INFO: dealloc: cuMemFree_v2 163584 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 52 bytes
INFO: dealloc: cuMemFree_v2 52 bytes
INFO: dealloc: cuMemFree_v2 312 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 27248 bytes
INFO: add pending dealloc: cuMemFree_v2 27248 bytes
INFO: add pending dealloc: cuMemFree_v2 163488 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 92 bytes
INFO: add pending dealloc: cuMemFree_v2 92 bytes
INFO: add pending dealloc: cuMemFree_v2 552 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cu

INFO: dealloc: cuMemFree_v2 576 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 27368 bytes
INFO: add pending dealloc: cuMemFree_v2 27368 bytes
INFO: add pending dealloc: cuMemFree_v2 164208 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 52 bytes
INFO: add pending dealloc: cuMemFree_v2 52 bytes
INFO: add pending dealloc: cuMemFree_v2 312 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 27368 bytes
INFO: dealloc: cuMemFree_v2 27368 bytes
INFO: dealloc: cuMemFree_v2 164208 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 52 bytes
INFO: dealloc: cuMemFree_v2 52 bytes
INFO: dealloc: cuMemFree_v2 312 bytes
INFO: dealloc: cuMemFree_v2 32 

INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 88 bytes
INFO: add pending dealloc: cuMemFree_v2 88 bytes
INFO: add pending dealloc: cuMemFree_v2 528 bytes
INFO: dealloc: cuMemFree_v2 504 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 27220 bytes
INFO: dealloc: cuMemFree_v2 27220 bytes
INFO: dealloc: cuMemFree_v2 163320 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 88 bytes
INFO: dealloc: cuMemFree_v2 88 bytes
INFO: dealloc: cuMemFree_v2 528 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 27324 bytes
INFO: add pending dealloc: cuMemFree_v2 27324 bytes
INFO: add pending dealloc: cuMemFree_v2 163944 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMe

INFO: dealloc: cuMemFree_v2 165048 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 104 bytes
INFO: add pending dealloc: cuMemFree_v2 104 bytes
INFO: add pending dealloc: cuMemFree_v2 624 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 27264 bytes
INFO: add pending dealloc: cuMemFree_v2 27264 bytes
INFO: add pending dealloc: cuMemFree_v2 163584 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 112 bytes
INFO: add pending dealloc: cuMemFree_v2 112 bytes
INFO: dealloc: cuMemFree_v2 104 bytes
INFO: dealloc: cuMemFree_v2 624 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 27264 bytes
INFO: dealloc: cuMemFree_v2 27264 bytes
INFO: dealloc: cuMemFree_v2 163584 bytes
INFO: dealloc: cuMemFre

INFO: add pending dealloc: cuMemFree_v2 27244 bytes
INFO: add pending dealloc: cuMemFree_v2 27244 bytes
INFO: add pending dealloc: cuMemFree_v2 163464 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 68 bytes
INFO: dealloc: cuMemFree_v2 68 bytes
INFO: dealloc: cuMemFree_v2 408 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: dealloc: cuMemFree_v2 27244 bytes
INFO: dealloc: cuMemFree_v2 27244 bytes
INFO: dealloc: cuMemFree_v2 163464 bytes
INFO: dealloc: cuMemFree_v2 32 bytes
INFO: dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 96 bytes
INFO: add pending dealloc: cuMemFree_v2 96 bytes
INFO: add pending dealloc: cuMemFree_v2 576 bytes
INFO: add pending dealloc: cuMemFree_v2 32 bytes
INFO: add pending dealloc: cuMemFree_v2 24 bytes
INFO: add pending dealloc: cuMemFree_v2 27224 bytes
INFO: add pending dealloc: cu

In [18]:
# Now use the fine-tunded model to run inference.

args = get_args_for_inference_example("./tmp_working_dir/finetuned/last.ckpt")
ckpt = model.load_checkpoint(args, validate_args=False)
result = model.run_inference(args, ckpt, False)

DEBUG: 7165 atoms and 1 coordinate set(s) were parsed in 0.07s.


Restoring from checkpoint: ./tmp_working_dir/finetuned/last.ckpt
Using the operator mean to aggregate the inferences.
Using checkpoint ./tmp_working_dir/finetuned/last.ckpt

Loading model from checkpoint ./tmp_working_dir/finetuned/last.ckpt

    Rotation #1
    Rotation #2


/gpfs/workspace/users/durraj/deepfrag2/collagen/core/molecules/mol.py:443: UserWarning: Internal rdmol has no conformers
  warnings.warn("Internal rdmol has no conformers")


Label set size: 556


Most Similar Matches:   0%|          | 0/1 [00:00<?, ?it/s]

In [19]:
result

{'most_similar': [['*C', 0.6220338344573975],
  ['*N', 0.5480952262878418],
  ['*CN', 0.48324668407440186],
  ['*CC', 0.460236132144928],
  ['*NC', 0.4554051160812378],
  ['*CCN', 0.424025297164917],
  ['*N(C)C', 0.41443145275115967],
  ['*C(C)N', 0.40668046474456787],
  ['*C#N', 0.3963017463684082],
  ['*CCC', 0.3836550712585449]],
 'fps': {'per_rot': [tensor([[3.7987e-02, 7.0182e-03, 3.4733e-04,  ..., 1.0812e-05, 1.0075e-04,
            1.9937e-01]], grad_fn=<SigmoidBackward0>),
   tensor([[9.4937e-02, 2.4549e-02, 1.6447e-03,  ..., 1.4361e-04, 8.7465e-04,
            3.4375e-01]], grad_fn=<SigmoidBackward0>)],
  'avg': tensor([[6.6462e-02, 1.5784e-02, 9.9602e-04,  ..., 7.7209e-05, 4.8770e-04,
           2.7156e-01]], grad_fn=<MeanBackward1>)}}